In [1]:
import os
import pandas as pd
import datetime
import re
import logging
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.ticker as ticker

logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')

# Function to list all chat files in the directory structure
def list_chat_files(date_directory):
    chat_files = []
    for date_folder in os.listdir(date_directory):
        date_path = os.path.join(date_directory, date_folder)
        if os.path.isdir(date_path):
            for team_folder in os.listdir(date_path):
                team_path = os.path.join(date_path, team_folder)
                if os.path.isdir(team_path):
                    for person_folder in os.listdir(team_path):
                        person_path = os.path.join(team_path, person_folder)
                        if os.path.isdir(person_path):
                            for file in os.listdir(person_path):
                                if file.endswith('.txt'):
                                    chat_files.append(os.path.join(person_path, file))
    return chat_files

def parse_chat_file(file_path, expected_date_minus_one):
    chat_data = []

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            message_match = re.match(r'(\d{2}/\d{2}/\d{2}, \d{1,2}:\d{2} [ap]m) - (.*?): (.*)', line)
            system_match = re.match(r'(\d{2}/\d{2}/\d{2}, \d{1,2}:\d{2} [ap]m) - (.*)', line)
            if message_match:
                date_time_str, sender, message = message_match.groups()
            elif system_match:
                date_time_str, info = system_match.groups()
                sender = None
            else:
                continue

            date_time = pd.to_datetime(date_time_str, format='%d/%m/%y, %I:%M %p')

            # Compare parsed date with the date one day before the expected date
            if date_time.date() != expected_date_minus_one:
                continue

            is_person = sender is not None and re.match(r'^[+\d\s-]+$', sender) is None
            chat_data.append((date_time, sender, is_person))
    return chat_data

# Function to create a template dataframe
def create_template_dataframe():
    times = [datetime.datetime(2000, 1, 1, 0, 0) + datetime.timedelta(minutes=1 * i) for i in range(1440)]
    intervals = [time.strftime('%I:%M %p') for time in times]
    df = pd.DataFrame(index=intervals)
    return df

def populate_dataframe(df, parsed_data, start_column_index):
    new_columns = {}  # Dictionary to hold new data before concatenation

    for entry in parsed_data:
        date_time, sender, is_person = entry
        interval_index = min((date_time.hour * 60 + date_time.minute) // 1, 1439)
        interval = df.index[interval_index]

        # Initialize columns in new_columns dictionary if not exist
        if (start_column_index not in new_columns):
            new_columns[start_column_index] = pd.Series(0, index=df.index)
        if (start_column_index + 1 not in new_columns):
            new_columns[start_column_index + 1] = pd.Series(0, index=df.index)

        # Populate the new_columns dictionary
        if is_person:
            new_columns[start_column_index].at[interval] = 1
        else:
            new_columns[start_column_index + 1].at[interval] = 1
    print(f"DataFrame after concatenation: {df.head(1)}")
    # Concatenate new columns to the DataFrame at once
    df = pd.concat([df, pd.DataFrame(new_columns)], axis=1)

    return df, start_column_index + 2

def process_person_chats(chat_files):
    dataframes = {}
    for file in chat_files:
        parts = file.split(os.sep)
        date_folder, person = parts[-4], parts[-2]

        try:
            folder_date = pd.to_datetime(date_folder, format='%Y-%m-%d').date()
        except ValueError:
            continue

        expected_date_minus_one = folder_date - datetime.timedelta(days=1)
        key = f"{folder_date.strftime('%Y-%m-%d')}_{person}"

        if key not in dataframes:
            dataframes[key] = create_template_dataframe()
            start_column_index = 0
        else:
            if not dataframes[key].columns.empty:
                start_column_index = max(dataframes[key].columns) + 1
            else:
                start_column_index = 0

        parsed_data = parse_chat_file(file, expected_date_minus_one)
        dataframes[key], start_column_index = populate_dataframe(dataframes[key], parsed_data, start_column_index)
    print(f"Matrix DataFrame for {key}: {dataframes[key].head()}")  # Debug print
    return dataframes


def count_active_chats_at_time(matrix_df, timestamp):
    # Format the timestamp to match the DataFrame's index format (%I:%M %p)
    interval = timestamp.strftime('%I:%M %p')
    logging.debug(f"Checking active chats at time: {interval}")  # Debugging print

    if interval in matrix_df.index:
        active_chats_count = matrix_df.loc[interval].sum()
        logging.debug(f"Active chats count: {active_chats_count}")  # Debugging print
        return active_chats_count
    else:
        logging.debug("No matching interval found")  # Debugging print
        return 0



# Function to list all chat files in the directory structure
def list_chat_files(date_directory):
    chat_files = []
    for date_folder in os.listdir(date_directory):
        date_path = os.path.join(date_directory, date_folder)
        if os.path.isdir(date_path):
            for team_folder in os.listdir(date_path):
                team_path = os.path.join(date_path, team_folder)
                if os.path.isdir(team_path):
                    for person_folder in os.listdir(team_path):
                        person_path = os.path.join(team_path, person_folder)
                        if os.path.isdir(person_path):
                            for file in os.listdir(person_path):
                                if file.endswith('.txt'):
                                    chat_files.append(os.path.join(person_path, file))
    return chat_files

def parse_chat_file_for_delay_analysis(file_path):
    # Extract person_name and date from the file path
    person_name = os.path.basename(os.path.dirname(file_path))
    folder_date_str = os.path.basename(os.path.dirname(os.path.dirname(os.path.dirname(file_path))))
    expected_date_minus_one = pd.to_datetime(folder_date_str, format='%Y-%m-%d').date() - datetime.timedelta(days=1)

    delay_messages = []

    with open(file_path, 'r', encoding='utf-8') as file:
        lines = file.readlines()

    last_person_msg_time = None
    last_person_msg_index = None

    for i, line in enumerate(lines):
        message_match = re.match(r'(\d{2}/\d{2}/\d{2}, \d{1,2}:\d{2} [ap]m) - (.*?): (.*)', line)
        if message_match:
            date_time_str, sender, message = message_match.groups()
            date_time = pd.to_datetime(date_time_str, format='%d/%m/%y, %I:%M %p')

            if date_time.date() != expected_date_minus_one:
                continue

            # Check if the sender is a person (not purely numeric or starting with +)
            is_person = sender is not None and not (sender.strip().isnumeric() or sender.startswith('+'))

            logging.info(f"Sender: {sender}, Is Person: {is_person}, Message: {message}")  # Debug line

            if is_person:
                if last_person_msg_time is not None:
                    # Calculate the time difference in minutes
                    time_diff_seconds = (date_time - last_person_msg_time).total_seconds()
                    time_diff_minutes = time_diff_seconds / 60
                    logging.info(f"Time Difference (minutes): {time_diff_minutes}")  # Debug line
                    if time_diff_minutes > 15:
                        # There is a delay
                        delay = True
                    else:
                        # No delay
                        delay = False
                        time_diff_minutes = None
                else:
                    # No previous message from a person
                    delay = False
                    time_diff_minutes = None
                last_person_msg_time = date_time
                last_person_msg_index = i
            else:
                # Not a message from a person
                delay = False
                time_diff_minutes = None

            if delay:
                # Fetch reference messages
                start_index = max(last_person_msg_index - 3, 0)
                end_index = min(i + 4, len(lines) - 1)
                reference_msgs = lines[start_index:end_index + 1]

                delay_messages.append((date_time, sender, message, delay, time_diff_minutes, reference_msgs))

    return delay_messages, file_path


def process_all_files_with_matrix(chat_files, matrix_dataframes):
    all_delay_messages = []

    for file_path in chat_files:
        logging.info(f"Processing file: {file_path}")  # Debug line
        delay_messages, file_path_from_function = parse_chat_file_for_delay_analysis(file_path)
        person_name = os.path.basename(os.path.dirname(file_path))
        matrix_df = matrix_dataframes.get(person_name)

        for message in delay_messages:
            timestamp, sender, msg, delay, time_diff_minutes, reference_msgs = message
            active_chats_count = count_active_chats_at_time(matrix_df, timestamp) if matrix_df is not None else 0
            all_delay_messages.append((timestamp, sender, msg, delay, time_diff_minutes, reference_msgs, active_chats_count))

    return all_delay_messages

def create_delay_data_dataframe_with_active_chats(all_delay_data):
    columns = ['Date', 'Person', 'Chat Group Name', 'Delay', 'Delay in Mins', 'Reference Messages', 'Active Chats at Time of Delay']
    df_data = []

    for delay_instance in all_delay_data:
        date_time, sender, message, delay, time_diff_minutes, reference_msgs, active_chats_count = delay_instance

        file_name = os.path.basename(reference_msgs[0])
        logging.info(f"Processing file name: {file_name}")  # Debugging line

        group_name_match = re.match(r'WhatsApp Chat with (.+?)\.txt', file_name)
        chat_group_name = group_name_match.group(1) if group_name_match else "Unknown Group"

        df_data.append([date_time, sender, chat_group_name, delay, time_diff_minutes, reference_msgs, active_chats_count])

    delay_df = pd.DataFrame(df_data, columns=columns)
    return delay_df

# Main Execution
date_directory = "C:\\Users\\maurice\\Documents\\Chat-Analyzer-V2\\Chat Folder from Drive\\drive-download-20231130T060206Z-001"
chat_files = list_chat_files(date_directory)
matrix_dataframes = process_person_chats(chat_files)
all_delay_data = process_all_files_with_matrix(chat_files, matrix_dataframes)
delay_analysis_df = create_delay_data_dataframe_with_active_chats(all_delay_data)

# Display the first few rows of the DataFrame
print(delay_analysis_df.head())


DataFrame after concatenation: Empty DataFrame
Columns: []
Index: [12:00 AM]
DataFrame after concatenation:           0  1
12:00 AM  0  0
DataFrame after concatenation:           0  1  2  3
12:00 AM  0  0  0  0
DataFrame after concatenation:           0  1  2  3  4  5
12:00 AM  0  0  0  0  0  0
DataFrame after concatenation:           0  1  2  3  4  5  6  7
12:00 AM  0  0  0  0  0  0  0  0
DataFrame after concatenation:           0  1  2  3  4  5  6  7  8  9
12:00 AM  0  0  0  0  0  0  0  0  0  0
DataFrame after concatenation:           0   1   2   3   4   5   6   7   8   9   10  11
12:00 AM   0   0   0   0   0   0   0   0   0   0   0   0
DataFrame after concatenation:           0   1   2   3   4   5   6   7   8   9   10  11  12  13
12:00 AM   0   0   0   0   0   0   0   0   0   0   0   0   0   0
DataFrame after concatenation:           0   1   2   3   4   5   6   7   8   9   10  11  12  13  14  15
12:00 AM   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
DataFrame after

DataFrame after concatenation:           0   1   2   3   4   5   6   7   8   9   ...  62  63  64  65  66  67  \
12:00 AM   0   0   0   0   0   0   0   0   0   0  ...   0   0   0   0   0   0   

          68  69  70  71  
12:00 AM   0   0   0   0  

[1 rows x 72 columns]
DataFrame after concatenation:           0   1   2   3   4   5   6   7   8   9   ...  64  65  66  67  68  69  \
12:00 AM   0   0   0   0   0   0   0   0   0   0  ...   0   0   0   0   0   0   

          70  71  72  73  
12:00 AM   0   0   0   0  

[1 rows x 74 columns]
DataFrame after concatenation:           0   1   2   3   4   5   6   7   8   9   ...  66  67  68  69  70  71  \
12:00 AM   0   0   0   0   0   0   0   0   0   0  ...   0   0   0   0   0   0   

          72  73  74  75  
12:00 AM   0   0   0   0  

[1 rows x 76 columns]
DataFrame after concatenation:           0   1   2   3   4   5   6   7   8   9   ...  68  69  70  71  72  73  \
12:00 AM   0   0   0   0   0   0   0   0   0   0  ...   0   0   0   0   0  

DataFrame after concatenation:           0    1    2    3    4    5    6    7    8    9    ...  132  133  \
12:00 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   

          134  135  136  137  138  139  140  141  
12:00 AM    0    0    0    0    0    0    0    0  

[1 rows x 142 columns]
DataFrame after concatenation:           0    1    2    3    4    5    6    7    8    9    ...  134  135  \
12:00 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   

          136  137  138  139  140  141  142  143  
12:00 AM    0    0    0    0    0    0    0    0  

[1 rows x 144 columns]
DataFrame after concatenation:           0    1    2    3    4    5    6    7    8    9    ...  136  137  \
12:00 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   

          138  139  140  141  142  143  144  145  
12:00 AM    0    0    0    0    0    0    0    0  

[1 rows x 146 columns]
DataFrame after concatenation:           0    1    2    3    4  

DataFrame after concatenation:           0    1    2    3    4    5    6    7    8    9    ...  190  191  \
12:00 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   

          192  193  194  195  196  197  198  199  
12:00 AM    0    0    0    0    0    0    0    0  

[1 rows x 200 columns]
DataFrame after concatenation:           0    1    2    3    4    5    6    7    8    9    ...  192  193  \
12:00 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   

          194  195  196  197  198  199  200  201  
12:00 AM    0    0    0    0    0    0    0    0  

[1 rows x 202 columns]
DataFrame after concatenation:           0    1    2    3    4    5    6    7    8    9    ...  194  195  \
12:00 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   

          196  197  198  199  200  201  202  203  
12:00 AM    0    0    0    0    0    0    0    0  

[1 rows x 204 columns]
DataFrame after concatenation:           0    1    2    3    4  

DataFrame after concatenation:           0   1   2   3   4   5   6   7   8   9   ...  52  53  54  55  56  57  \
12:00 AM   0   0   0   0   0   0   0   0   0   0  ...   0   0   0   0   0   0   

          58  59  60  61  
12:00 AM   0   0   0   0  

[1 rows x 62 columns]
DataFrame after concatenation:           0   1   2   3   4   5   6   7   8   9   ...  54  55  56  57  58  59  \
12:00 AM   0   0   0   0   0   0   0   0   0   0  ...   0   0   0   0   0   0   

          60  61  62  63  
12:00 AM   0   0   0   0  

[1 rows x 64 columns]
DataFrame after concatenation:           0   1   2   3   4   5   6   7   8   9   ...  56  57  58  59  60  61  \
12:00 AM   0   0   0   0   0   0   0   0   0   0  ...   0   0   0   0   0   0   

          62  63  64  65  
12:00 AM   0   0   0   0  

[1 rows x 66 columns]
DataFrame after concatenation:           0   1   2   3   4   5   6   7   8   9   ...  58  59  60  61  62  63  \
12:00 AM   0   0   0   0   0   0   0   0   0   0  ...   0   0   0   0   0  

...

2023-11-30 15:20:59,409 - INFO - Processing file name: 23, 9:59 am - Shubham Madhwal: Good Morning Everyone, 

2023-11-30 15:20:59,409 - INFO - Processing file name: Please excuse me for being unavailable for the past few days as there was a family emergency.

2023-11-30 15:20:59,409 - INFO - Processing file name: 23, 10:14 am - +263 77 562 9724: Good morning, Ashleigh has exams today he's not available

2023-11-30 15:20:59,409 - INFO - Processing file name: 23, 11:09 am - +263 77 562 9724: Thank you

2023-11-30 15:20:59,409 - INFO - Processing file name: 23, 11:26 am - Shubham Madhwal: `Why have you been so inactive lately?

2023-11-30 15:20:59,409 - INFO - Processing file name: 23, 5:59 pm - +263 77 690 4354: I'm fine sir, I'm sorry i wasn't on line since morning

2023-11-30 15:20:59,409 - INFO - Processing file name: 23, 8:13 am - Shubham Madhwal: I am  doing great please

2023-11-30 15:20:59,409 - INFO - Processing file name: 23, 8:55 am - +263 77 690 4354: Today i don't have quest

2023-11-30 15:20:59,440 - INFO - Processing file name: 23, 4:38 pm - +27 73 055 2749: Affordability through guaranteed scholarships  because through the acceptance of this program  a candidate is guaranteed a minimum scholarship of 50-100 percent of their tuition fee,,,this makes me to save bigger amounts in the application

2023-11-30 15:20:59,440 - INFO - Processing file name: Please excuse me for being unavailable for the past few days as there was a family emergency.

2023-11-30 15:20:59,440 - INFO - Processing file name: 23, 9:44 am - Shubham Madhwal: Good Morning Everyone, 

2023-11-30 15:20:59,440 - INFO - Processing file name: Please excuse me for being unavailable for the past few days as there was a family emergency.

2023-11-30 15:20:59,440 - INFO - Processing file name: 23, 11:23 am - +27 71 073 2014: Still busy at work

2023-11-30 15:20:59,440 - INFO - Processing file name: 23, 11:58 am - +27 71 073 2014: Check me at 16H00

2023-11-30 15:20:59,440 - INFO - Processing file 

2023-11-30 15:20:59,487 - INFO - Processing file name: 

2023-11-30 15:20:59,487 - INFO - Processing file name: 23, 11:42 am - +260 95 3411232: That's awesome news

2023-11-30 15:20:59,487 - INFO - Processing file name: Please excuse me for being unavailable for the past few days as there was a family emergency.

2023-11-30 15:20:59,487 - INFO - Processing file name: 23, 2:51 pm - Shubham Madhwal: I am doing grreat please

2023-11-30 15:20:59,487 - INFO - Processing file name: 23, 2:52 pm - +263 78 085 5216: Yes I am available

2023-11-30 15:20:59,487 - INFO - Processing file name: 23, 4:09 pm - +263 78 085 5216: Yeah the ideas of the program are just great..and is what I was really looking for all along

2023-11-30 15:20:59,487 - INFO - Processing file name: 23, 4:39 pm - Shubham Madhwal: This registration fee($500-$1000) isn’t an additional amount as it will be waived off from your First year’s Fee thereby making it a part of the cost of education itself after that, the remaining has

2023-11-30 15:20:59,527 - INFO - Processing file name: 23, 1:14 pm - +260 97 6182543: Yes sir I am very much available untill 14.30

2023-11-30 15:20:59,527 - INFO - Processing file name: 23, 1:38 pm - +260 96 3408171: Mr Shubham sir this is Stermon's father, he is waiting for you to start the session

2023-11-30 15:20:59,528 - INFO - Processing file name: The program assist deserving students to access high quality tertiary education at affordable fees.

2023-11-30 15:20:59,529 - INFO - Processing file name: The process to be followed goes like this.Step 1 is the personalized counseling session followed by step2, the eligibility check test and interview then step3 where you get accepted in the edoofa program. Step4 you get enrolled into the edoofa program then step5 is when the admission process starts and then step6 you get your admission letter and visa

2023-11-30 15:20:59,530 - INFO - Processing file name: 23, 10:20 am - Shubham Madhwal: I am doing great pelase

2023-11-30 15:20:5

                 Date        Person Chat Group Name  Delay  Delay in Mins  \
0 2023-11-29 14:23:00  Aditi Edoofa   Unknown Group   True          205.0   
1 2023-11-29 13:51:00  Aditi Edoofa   Unknown Group   True           17.0   
2 2023-11-29 15:19:00  Aditi Edoofa   Unknown Group   True           88.0   
3 2023-11-29 14:52:00  Aditi Edoofa   Unknown Group   True           79.0   
4 2023-11-29 15:17:00  Aditi Edoofa   Unknown Group   True           25.0   

                                  Reference Messages  \
0  [\n, Please let me know his availability.\n, 2...   
1  [29/11/23, 1:34 pm - Aditi Edoofa: Good day Al...   
2  [29/11/23, 1:51 pm - +27 64 621 2214: Okay mam...   
3  [\n, Let's begin with today's session🚀\n, 29/1...   
4  [Thanks for asking,\n, 29/11/23, 2:52 pm - Adi...   

   Active Chats at Time of Delay  
0                              0  
1                              0  
2                              0  
3                              0  
4                        

In [2]:
delay_analysis_df.to_csv("delays.csv", index=False)